# Performance RNN
## Douglas Eck
This notebook shows you how to generate new performed compositions from a trained Performance RNN model. You'll see how to download a bundle containing a pre-trained model, instantiate and initialize the model and generate new polyphonic performances. The notebook also shows some hyperparameters useful for controlling generation, such as ``temperature``.

To hear the performances it is useful to have fluidsynth and pyfluidsynth installed. One way to install fluidsynth on OS X is via homebrew: ``brew install fluidsynth``.  One way to install pyfluidsynth is via pip: ``pip install pyfluidsynth``.

In [66]:
import os
import magenta
from magenta.models.drums_rnn import drums_rnn_sequence_generator
from magenta.protobuf import generator_pb2
from magenta.protobuf import music_pb2

import magenta.music as mm

# Constants.
BUNDLE_DIR = '/home/jovyan/models/'
MODEL_NAME = 'drum_kit'
BUNDLE_NAME = 'drum_kit_rnn.mag'

In [18]:
mm.notebook_utils.download_bundle(BUNDLE_NAME, BUNDLE_DIR)
bundle = mm.sequence_generator_bundle.read_bundle_file(os.path.join(BUNDLE_DIR, BUNDLE_NAME))

In [135]:
generator_map = drums_rnn_sequence_generator.get_generator_map()
generator = generator_map[MODEL_NAME](checkpoint=None, bundle=bundle)

In [177]:
generator.initialize()
generator_options = generator_pb2.GeneratorOptions()
generator_options.args['temperature'].float_value = 1.15  # Higher is more random; 1.0 is default.
generator_options.args['beam_size'].int_value = 4

In [178]:
primer_drums = magenta.music.DrumTrack([frozenset(pitches) for pitches in [(43, 66), (), (41,)]])
qpm = 160.0
primer_sequence = primer_drums.to_sequence(qpm=qpm)

In [179]:
seconds_per_step = 120.0 / qpm / generator.steps_per_quarter
total_seconds = 256 * seconds_per_step
last_end_time = (max(n.end_time for n in primer_sequence.notes)
                 if primer_sequence.notes else 0)
generate_section = generator_options.generate_sections.add(
    start_time=last_end_time + seconds_per_step,
    end_time=total_seconds)

In [180]:
sequence = generator.generate(primer_sequence, generator_options)

INFO:tensorflow:Beam search yields sequence with log-likelihood: -840.780090 


In [181]:
# Play and view this masterpiece.
mm.plot_sequence(sequence)
mm.play_sequence(sequence, mm.midi_synth.fluidsynth)

Loading BokehJS ...